#  Consignes

## Description

Ouvrir le fichier ks-projects-201801.csv, il recense environ 100 000 projets KickStarter. Intégrer les données directement avec L'API Python dans une base de données Mongo. 

Il conviendra de bien spécifier manuellement l'ID du document. Pensez aussi à bien formatter le type des données pour profiter des méthodes implémentées par Mongo. L'ensemble de données n'est pas forcément nécessaire, c'est à vous de créer votre modèle de données.

## Questions

- 1) Récupérer les 5 projets ayant reçu le plus de promesse de dons.
- 2) Compter le nombre de projets ayant atteint leur but.
- 3) Compter le nombre de projets pour chaque catégorie.
- 4) Compter le nombre de projets français ayant été instanciés avant 2016.
- 5) Récupérer les projets américains ayant demandé plus de 200 000 dollars.
- 6) Compter le nombre de projet ayant "Sport" dans leur nom

In [1]:
import pandas as pd
import pymongo

In [2]:
client = pymongo.MongoClient()
database = client['exercices']
collection = database['kickstarter']

In [3]:
df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")
df_ks.head(10)

C:\Users\natha\AppData\Local\Temp\ipykernel_332\182781903.py:1: DtypeWarning: Columns (6,8,10,12) have mixed types. Specify dtype option on import or set low_memory=False.
  df_ks = pd.read_csv("./data/ks-projects-201801-sample.csv")


ID                                               name  \
0   872782264    Scott Cooper's Solo CD "A Leg Trick" (Canceled)   
1  1326492673                                    Ohceola jewelry   
2  1688410639  Sluff Off & Harald: Two latest EGGs are Classi...   
3   156812982  SketchPlanner: Create and Plan- all in one bea...   
4  1835968190    Proven sales with custom motorcycle accessories   
5  1771789139                                   Room For Growth!   
6  1301627822          Build a mini Udemy with Laravel and Vuejs   
7   881336601                                         Applitizer   
8  1669374237  Help I Am Wolves fund their first album "ABCD"...   
9   556821416        Eco  Bamboo Underwear funding....GOT WOOD ?   

         category main_category currency    deadline      goal  \
0            Rock         Music      USD  2011-09-16    2000.0   
1         Fashion       Fashion      USD  2012-08-22   18000.0   
2  Tabletop Games         Games      USD  2016-07-19    2000.0   
3       Art Books    Publishing      USD  2017-09-27   13000.0   
4       Sculpture           Art      CAD  2016-02-24    5000.0   
5         Couture       Fashion      USD  2016-05-02    2000.0   
6             Web    Technology      CAD  2018-01-11    3000.0   
7        Software    Technology      HKD  2017-08-20  100000.0   
8           Music         Music      EUR  2017-12-04    1000.0   
9         Fashion       Fashion      GBP  2012-12-13    9500.0   

              launched  pledged       state backers country  usd pledged  \
0  2011-08-17 06:31:31   1145.0    canceled      24      US       1145.0   
1  2012-07-23 20:46:48   1851.0      failed      28      US       1851.0   
2  2016-07-01 21:55:54   7534.0  successful     254      US       3796.0   
3  2017-08-28 15:47:02  16298.0  successful     367      US       2670.0   
4  2016-01-25 17:37:10      1.0      failed       1      CA     0.708148   
5  2016-04-11 18:15:00      6.0      failed       2      US          6.0   
6  2017-12-12 01:37:26    155.0        live       7      CA    15.563996   
7  2017-07-21 16:50:05   1000.0      failed       1      HK    128.08538   
8  2017-10-27 16:55:47   1465.0  successful      46      BE          0.0   
9  2012-11-13 10:58:34   1212.0      failed      43      GB  1928.137119   

   usd_pledged_real  
0       1145.000000  
1       1851.000000  
2       7534.000000  
3      16298.000000  
4          0.738225  
5          6.000000  
6        123.811806  
7        127.831467  
8       1720.210418  
9       1953.672808

Ce warning intervient lorsque pandas n'arrive pas à inférer le type de données. Il est sympa il précise les colones 6,8,10,12. 

In [4]:
df_ks.columns[[6,8,10,12]]

Index(['goal', 'pledged', 'backers', 'usd pledged'], dtype='object')

## Question 0

### Netoyer les données

In [6]:
df_ks.dtypes

ID                    int64
name                 object
category             object
main_category        object
currency             object
deadline             object
goal                 object
launched             object
pledged              object
state                object
backers              object
country              object
usd pledged          object
usd_pledged_real    float64
dtype: object

In [75]:
df_ks.dropna(subset=['deadline', 'launched'], inplace=True)

print(df_ks['deadline'].isna().sum())
print(df_ks['launched'].isna().sum())

0
0


In [76]:

df_ks['backers'] = pd.to_numeric(df_ks['backers'], errors='coerce')
print(df_ks[df_ks['backers'].isna()])
# Remplacer les NaN par 0
df_ks['backers'] = df_ks['backers'].fillna(0).astype(int)
# Convertir les valeurs non numériques en NaN
df_ks['goal'] = pd.to_numeric(df_ks['goal'], errors='coerce')
df_ks['goal'] = df_ks['goal'].fillna(0).astype(float)

df_ks['pledged'] = pd.to_numeric(df_ks['pledged'], errors='coerce')
df_ks['pledged'] = df_ks['pledged'].fillna(0).astype(float)

df_ks['usd pledged'] = pd.to_numeric(df_ks['usd pledged'], errors='coerce')
df_ks['usd pledged'] = df_ks['usd pledged'].fillna(0).astype(float)


Empty DataFrame
Columns: [ID, name, category, main_category, currency, deadline, goal, launched, pledged, state, backers, country, usd pledged, usd_pledged_real]
Index: []


In [77]:
df_ks['launched']=pd.to_datetime(df_ks['launched'],errors='coerce')
df_ks['deadline']=pd.to_datetime(df_ks['deadline'],errors='coerce')
df_ks['backers']=df_ks['backers'].astype(int)
df_ks['goal']=df_ks['goal'].astype(float)
df_ks['pledged']=df_ks['pledged'].astype(float)
df_ks['usd pledged']=df_ks['usd pledged'].astype(float)


In [78]:
df_ks.dtypes

ID                           int64
name                        object
category                    object
main_category               object
currency                    object
deadline            datetime64[ns]
goal                       float64
launched            datetime64[ns]
pledged                    float64
state                       object
backers                      int64
country                     object
usd pledged                float64
usd_pledged_real           float64
dtype: object

### Importer les données

In [79]:
data_dict = df_ks.to_dict("records")
# Insérer les données dans la collection
collection.insert_many(data_dict)

InsertManyResult([ObjectId('67585cb8359466474cb91f14'), ObjectId('67585cb8359466474cb91f15'), ObjectId('67585cb8359466474cb91f16'), ObjectId('67585cb8359466474cb91f17'), ObjectId('67585cb8359466474cb91f18'), ObjectId('67585cb8359466474cb91f19'), ObjectId('67585cb8359466474cb91f1a'), ObjectId('67585cb8359466474cb91f1b'), ObjectId('67585cb8359466474cb91f1c'), ObjectId('67585cb8359466474cb91f1d'), ObjectId('67585cb8359466474cb91f1e'), ObjectId('67585cb8359466474cb91f1f'), ObjectId('67585cb8359466474cb91f20'), ObjectId('67585cb8359466474cb91f21'), ObjectId('67585cb8359466474cb91f22'), ObjectId('67585cb8359466474cb91f23'), ObjectId('67585cb8359466474cb91f24'), ObjectId('67585cb8359466474cb91f25'), ObjectId('67585cb8359466474cb91f26'), ObjectId('67585cb8359466474cb91f27'), ObjectId('67585cb8359466474cb91f28'), ObjectId('67585cb8359466474cb91f29'), ObjectId('67585cb8359466474cb91f2a'), ObjectId('67585cb8359466474cb91f2b'), ObjectId('67585cb8359466474cb91f2c'), ObjectId('67585cb8359466474cb91f

## Question 1  

In [98]:
top_projet=collection.find().sort("backers",-1).limit(5)
for project in top_projet:
    print(project)

{'_id': ObjectId('67585cb9359466474cbad981'), 'ID': 1386523707, 'name': 'Fidget Cube: A Vinyl Desk Toy', 'category': 'Product Design', 'main_category': 'Design', 'currency': 'USD', 'deadline': datetime.datetime(2016, 10, 20, 0, 0), 'goal': 15000.0, 'launched': datetime.datetime(2016, 8, 30, 22, 2, 9), 'pledged': 6465690.3, 'state': 'successful', 'backers': 154926, 'country': 'US', 'usd pledged': 13770.0, 'usd_pledged_real': 6465690.3}
{'_id': ObjectId('67585cb9359466474cb9fdeb'), 'ID': 1755266685, 'name': 'The Veronica Mars Movie Project', 'category': 'Narrative Film', 'main_category': 'Film & Video', 'currency': 'USD', 'deadline': datetime.datetime(2013, 4, 13, 0, 0), 'goal': 2000000.0, 'launched': datetime.datetime(2013, 3, 13, 15, 42, 22), 'pledged': 5702153.38, 'state': 'successful', 'backers': 91585, 'country': 'US', 'usd pledged': 5702153.38, 'usd_pledged_real': 5702153.38}
{'_id': ObjectId('67585cb9359466474cba77ad'), 'ID': 286165030, 'name': 'Torment: Tides of Numenera', 'categ

## Question 2

In [101]:
succesful_projet=collection.count_documents({'state':'successful'})
print(succesful_projet)

53040


## Question 3

In [110]:
projetParCategorie=collection.aggregate([
    {"$group": {
        "_id": "$category",        # Grouper par la catégorie
        "NombreProjetParCategorie": {"$sum": 1}  # Compter le nombre d'occurrences par catégorie
    }}
])

for i in projetParCategorie:
    print(i)


{'_id': 'Software', 'NombreProjetParCategorie': 1194}
{'_id': 'Mobile Games', 'NombreProjetParCategorie': 650}
{'_id': 'Gaming Hardware', 'NombreProjetParCategorie': 178}
{'_id': 'Musical', 'NombreProjetParCategorie': 367}
{'_id': "Farmer's Markets", 'NombreProjetParCategorie': 175}
{'_id': 'Art', 'NombreProjetParCategorie': 3358}
{'_id': 'Installations', 'NombreProjetParCategorie': 178}
{'_id': 'Wearables', 'NombreProjetParCategorie': 508}
{'_id': 'R&B', 'NombreProjetParCategorie': 172}
{'_id': 'Nature', 'NombreProjetParCategorie': 219}
{'_id': 'Romance', 'NombreProjetParCategorie': 74}
{'_id': 'Fine Art', 'NombreProjetParCategorie': 291}
{'_id': 'Video', 'NombreProjetParCategorie': 147}
{'_id': 'Comics', 'NombreProjetParCategorie': 1931}
{'_id': "Children's Books", 'NombreProjetParCategorie': 2686}
{'_id': 'Animation', 'NombreProjetParCategorie': 1017}
{'_id': 'Narrative Film', 'NombreProjetParCategorie': 2099}
{'_id': 'Public Art', 'NombreProjetParCategorie': 1248}
{'_id': 'World Mu

## Question 4

In [120]:
df_ks['launched']

0        2011-08-17 06:31:31
1        2012-07-23 20:46:48
2        2016-07-01 21:55:54
3        2017-08-28 15:47:02
4        2016-01-25 17:37:10
                 ...        
149995   2014-10-14 20:44:37
149996   2012-04-18 04:42:47
149997   2013-01-16 00:53:32
149998   2011-04-27 01:22:52
149999   2016-04-03 08:01:57
Name: launched, Length: 149999, dtype: datetime64[ns]

In [131]:
from datetime import datetime

# Créer un objet datetime pour la date limite 2016-01-01
date_limit = datetime(2016, 1, 1)
frProjetAvant2016 = collection.count_documents({
    "$and": [
        {'country': 'FR'},
        {'launched': {'$lt': date_limit}}  
    ]
})

print(frProjetAvant2016)


330


## Question 5

In [139]:
UsProjet200k = collection.find({
    "$and": [
        {'country': 'US'},
        {'usd_pledged_real': {'$gt': 200000.0}}  
    ]
})
count_us_200k = collection.count_documents({
    "$and": [
        {'country': 'US'},
        {'usd_pledged_real': {'$gt': 200000.0}}
    ]
})

print("Nombre de projet US ayant recu plus de 200k: ",count_us_200k)

for i in UsProjet200k:
    
    print(i)

Nombre de projet US ayant recu plus de 200k:  658
{'_id': ObjectId('67585cb8359466474cb91f43'), 'ID': 217543389, 'name': 'The uKeg Pressurized Growler for Fresh Beer', 'category': 'Drinks', 'main_category': 'Food', 'currency': 'USD', 'deadline': datetime.datetime(2014, 12, 8, 0, 0), 'goal': 75000.0, 'launched': datetime.datetime(2014, 10, 15, 6, 34, 48), 'pledged': 1559525.68, 'state': 'successful', 'backers': 10293, 'country': 'US', 'usd pledged': 1559525.68, 'usd_pledged_real': 1559525.68}
{'_id': ObjectId('67585cb8359466474cb91fd3'), 'ID': 909248984, 'name': 'Redux COURG - Hybrid Watches with Missions to Tackle', 'category': 'Product Design', 'main_category': 'Design', 'currency': 'USD', 'deadline': datetime.datetime(2015, 8, 20, 0, 0), 'goal': 30000.0, 'launched': datetime.datetime(2015, 7, 21, 19, 1, 41), 'pledged': 692912.0, 'state': 'successful', 'backers': 2200, 'country': 'US', 'usd pledged': 692912.0, 'usd_pledged_real': 692912.0}
{'_id': ObjectId('67585cb8359466474cb92081'),

## Question 6 

In [143]:
SportDansNom =collection.count_documents({
    "name": {"$regex": "Sport", "$options": "i"}  # "i" pour rendre la recherche insensible à la casse
})

print(SportDansNom)

SportDansNom =collection.find({
    "name": {"$regex": "Sport", "$options": "i"}  # "i" pour rendre la recherche insensible à la casse
}).limit(10)
for i in SportDansNom:
    print(i)

502
{'_id': ObjectId('67585cb8359466474cb92313'), 'ID': 802281658, 'name': 'Sportswear range', 'category': 'Apparel', 'main_category': 'Fashion', 'currency': 'AUD', 'deadline': datetime.datetime(2014, 8, 23, 0, 0), 'goal': 25000.0, 'launched': datetime.datetime(2014, 7, 24, 5, 14, 52), 'pledged': 20.0, 'state': 'failed', 'backers': 1, 'country': 'AU', 'usd pledged': 18.7569048, 'usd_pledged_real': 18.67588010084976}
{'_id': ObjectId('67585cb8359466474cb924dc'), 'ID': 2143543297, 'name': 'SPORTSFRIENDS featuring Johann Sebastian Joust', 'category': 'Video Games', 'main_category': 'Games', 'currency': 'USD', 'deadline': datetime.datetime(2012, 12, 10, 0, 0), 'goal': 150000.0, 'launched': datetime.datetime(2012, 11, 8, 22, 55, 34), 'pledged': 152451.25, 'state': 'successful', 'backers': 4146, 'country': 'US', 'usd pledged': 152451.25, 'usd_pledged_real': 152451.25}
{'_id': ObjectId('67585cb8359466474cb924f2'), 'ID': 1838460041, 'name': 'Mount Systems for Recreation Sports & Film (GoPro) L